# Generating points

We want to generate points on a sphere, where points will be as closely together while sthill "covering" the sphere. It is obvous this will be achived when in the comlex distances between neighbouring points will be equidistant/ we want wo place them so they are evenly distributed around the sphere. 

That is impossible if any number of points where points don't match the numbber of verteces of of platonic solid (4,6,8,12,20). However we can get close. 

We will look at 2 aproaches a a simulation for the Thomson Problem and a deterministic way using Fibonacci lattices.



## Data representations

We will represent points with a vector of points where a point is a vector in itself/ am matrix of size 50x3

In [111]:
function fibonacci_sphere(N::Integer)
    pts = zeros(Float64, N, 3)
    ϕ = π * (sqrt(5)-1)             # golden angle in radians
    for k in 0:(N-1)
        z = 1.0 - 2.0*(k)/((N))     # from 1 to -1
        r = sqrt( 1 - z*z)          # x2 +y2 = 1 - z2, x2+y2=r2
        θ = ϕ * k  # golden angle increment
        x = r * cos(θ)
        y = r * sin(θ)
        pts[k+1, :] = [x, y, z]
    end
    return pts
end

fibonacci_sphere (generic function with 1 method)

In [112]:
pts=fibonacci_sphere(50)

50×3 Matrix{Float64}:
  0.0         0.0         1.0
 -0.206463   -0.189137    0.96
  0.0342637   0.390418    0.92
  0.288992   -0.376939    0.88
 -0.534292    0.0945088   0.84
  0.506253    0.322037    0.8
 -0.168723   -0.627641    0.76
 -0.319858    0.615866    0.72
  0.688722   -0.25152     0.68
 -0.710244   -0.293178    0.64
  0.339077    0.724587    0.6
  0.247954   -0.790518    0.56
 -0.739034    0.428285    0.52
  ⋮                      
 -0.850521    0.0788261  -0.52
  0.659944    0.500874   -0.56
 -0.143187   -0.787082   -0.6
 -0.409241    0.650325   -0.64
  0.707137   -0.193797   -0.68
 -0.617419   -0.316849   -0.72
  0.225924    0.609392   -0.76
  0.226226   -0.555718   -0.8
 -0.490311    0.232368   -0.84
  0.453891    0.139939   -0.88
 -0.198163   -0.338129   -0.92
 -0.0587867   0.273759   -0.96

### Thomson Simulation

In [113]:
using LinearAlgebra
function grad(pts)
    n=size(pts, 1)
    F=zeros(Float64, n, 3)
    for i in 1:(n-1)
        p_i = pts[i,:]
        for j in (i+1):n
            p_j = pts[j, :]
            v=p_i-p_j
            d=norm(p_i-p_j)
            F[i,:].+=(2*v/(d^2))
            F[j,:].-=(2*v/(d^2))
        end 
    end
    return F
end

function relax_on_sphere(pts; steps = 10000, dt=0.005, cooling = 0.999, text=false)
    for step in 1:steps
        F=grad(pts)
        pts.+=dt .* F
        for i in 1:size(pts,1)
            pts[i,:] ./= norm(pts[i,:])
        end
        dt *= cooling
    
        if text && (step % 50 == 0 || step == 1)
            # measure minimal pairwise distance
            md = minimal_pairwise_distance(pts)
            println("it=$step dt=$(round(dt, sigdigits=3)) min-dist=$(round(md, sigdigits=6))")
        end
    end
end

function minimal_pairwise_distance(pts)
    N = size(pts,1)
    md = Inf
    for i in 1:N-1
        for j in i+1:N
            d = norm(pts[i,:] - pts[j,:])
            if d < md
                md = d
            end
        end
    end
    return md
end


minimal_pairwise_distance (generic function with 1 method)

In [119]:
using WGLMakie, ColorTypes

function plot_sphere_with_points_web(pts, edges)
    fig = Figure(size=(800, 800))
    ax = Axis3(fig[1,1], aspect=:data)

    # Sphere mesh
    θ = range(0, 2π, length=80)
    φ = range(0, π, length=40)
    x = [sin(phi)*cos(th) for phi in φ, th in θ]
    y = [sin(phi)*sin(th) for phi in φ, th in θ]
    z = [cos(phi) for phi in φ, th in θ]

    # Make sphere transparent
    surface!(ax, x, y, z, color=RGBA(0.5, 0.7, 1.0, 0.2), transparency=true)

    # Points
    scatter!(ax, pts[:,1], pts[:,2], pts[:,3], color=RGBA(1,0,0,1), markersize=15)

    # Edges
    for (i,j) in edges
        lines!(ax, [pts[i,1], pts[j,1]], [pts[i,2], pts[j,2]], [pts[i,3], pts[j,3]], color=:black, linewidth=2)
    end

    fig
end

fig = plot_sphere_with_points_web(pts, [])


In [115]:
relax_on_sphere(pts,text=true)

it=1 dt=0.005 min-dist=0.318395
it=50 dt=0.00476 min-dist=0.46674
it=100 dt=0.00452 min-dist=0.475306
it=150 dt=0.0043 min-dist=0.477806
it=200 dt=0.00409 min-dist=0.476801
it=250 dt=0.00389 min-dist=0.47609
it=300 dt=0.0037 min-dist=0.475649
it=350 dt=0.00352 min-dist=0.475396
it=400 dt=0.00335 min-dist=0.475267
it=450 dt=0.00319 min-dist=0.475219
it=500 dt=0.00303 min-dist=0.475226
it=550 dt=0.00288 min-dist=0.475271
it=600 dt=0.00274 min-dist=0.475342
it=650 dt=0.00261 min-dist=0.475432
it=700 dt=0.00248 min-dist=0.475534
it=750 dt=0.00236 min-dist=0.475645
it=800 dt=0.00225 min-dist=0.475762
it=850 dt=0.00214 min-dist=0.475881
it=900 dt=0.00203 min-dist=0.476001
it=950 dt=0.00193 min-dist=0.476121
it=1000 dt=0.00184 min-dist=0.476239
it=1050 dt=0.00175 min-dist=0.476355
it=1100 dt=0.00166 min-dist=0.476469
it=1150 dt=0.00158 min-dist=0.476579
it=1200 dt=0.00151 min-dist=0.476686
it=1250 dt=0.00143 min-dist=0.476789
it=1300 dt=0.00136 min-dist=0.476889
it=1350 dt=0.0013 min-dist=0.4

In [118]:

fig = plot_sphere_with_points_web(pts, [])